## Starting abstract world
> Its been little hard to start with tensorflow tfrecord, but neverthless, journey is Good

<font color=blue|red|green>Using cats and dogs dataset</font>

`Using following links`

<https://www.skcript.com/svr/why-every-tensorflow-developer-should-know-about-tfrecord/>

<https://github.com/tensorflow/models/blob/master/tutorials/image/cifar10_estimator/generate_cifar10_tfrecords.py>

<http://machinelearninguru.com/deep_learning/tensorflow/basics/tfrecord/tfrecord.html>

<https://towardsdatascience.com/working-with-tfrecords-and-tf-train-example-36d111b3ff4d>

In [1]:
#invoking required packages

In [2]:
import glob
import numpy as np
import tensorflow as tf
import os
import cv2
import sys

In [3]:
#finding out the path
path = os.getcwd()
print(path)

C:\Users\aim\Downloads\cat-and-dog


In [4]:
os.listdir()

['.ipynb_checkpoints',
 'cats',
 'dogs',
 'test_set.zip',
 'training_set',
 'training_set.zip',
 'Understanding TFRecords.ipynb']

In [5]:
type(glob.glob(path))

list

In [6]:
#interested in training_set folder
#made sure that very few images present here
path = path +'\\'+ os.listdir()[4]

In [7]:
path

'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set'

In [8]:
#finding out root directory and file..
#how exactly it iterates
#its hirerachial, first selects given path as root and subfolder as directory and any files inside it
#the gets inside directory, and considers that directory as roots, and this goes on

for r, d, f in os.walk(path):
    print(r)
    print(d)
    print(f)
    print(len(f))

C:\Users\aim\Downloads\cat-and-dog\training_set
['cats', 'dogs']
[]
0
C:\Users\aim\Downloads\cat-and-dog\training_set\cats
[]
['cat.1.jpg', 'cat.2.jpg', 'cat.3.jpg', 'cat.4.jpg']
4
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs
[]
['dog.1.jpg', 'dog.2.jpg', 'dog.3.jpg', 'dog.4.jpg', 'dog.5.jpg']
5


In [9]:
#creating list of all files which I'm interseted in
# we want to store these file addresses in list
train_addr = []
# also creating labels
labels = []
for r, d, f in os.walk(path):
    for file in f:
        if 'cat' in file:
            labels.append(0)
            print(r+'\\'+file)
            train_addr.append(r+'\\'+file)
        elif 'dog' in file:
            labels.append(1)
            print(r+'\\'+file)
            train_addr.append(r+'\\'+file)

C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.1.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.2.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.3.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.4.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.1.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.2.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.3.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.4.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.5.jpg


In [10]:
train_addr

['C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\cats\\cat.1.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\cats\\cat.2.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\cats\\cat.3.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\cats\\cat.4.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\dogs\\dog.1.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\dogs\\dog.2.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\dogs\\dog.3.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\dogs\\dog.4.jpg',
 'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\dogs\\dog.5.jpg']

In [11]:
train_addr[0]

'C:\\Users\\aim\\Downloads\\cat-and-dog\\training_set\\cats\\cat.1.jpg'

In [12]:
len(labels)

9

In [13]:
label = np.array(labels)

In [14]:
len(label)

9

In [15]:
np.sum(label == 1)

5

In [16]:
np.sum(label==0)

4

In [17]:
def load_image(adr):
    #read image and resize to (224, 224)
    #cv2 
    print(adr)
    img = cv2.imread(adr)#returns numpy array from given address
    img = cv2.resize(img, (224, 224))#resize
    
    img = img.astype(np.float32)#numpy array converted into float32
    return img

In [18]:
#convert data into features
"""TFRecords ca take data in only three datatypes,
    1) Int64List
    2) BytesList
    3) FloatList
    
    whatever data we have should be converted into this format using 
    tf.train.Int64List, tf.train.BytesList, tf.train.FloatList
    
    tf.train.Feature takes only these protocol buffers
    
    we create dictionay of key and value, 
    where, 
        key is string
        value is buffer of type tf.train.Feature
        
    this dictionary is passed to only field in tf.train.Features called feature
    
    tf.train.Features is given to only field of tf.train.Example called features
    
    this protocol buffer is serialized using SerializeToString and then written using writer of 
    tf.python_io.TFRecordWriter
"""
def _int64_feature(value):
    return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))
def _bytes_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))
def _float_feature(value):
    """Returns a float_list from a float / double."""
    return tf.train.Feature(float_list=tf.train.FloatList(value=[value]))

In [19]:
train_filename = 'train.tfrecords'  # address to save the TFRecords file
# open the TFRecords file
writer = tf.python_io.TFRecordWriter(train_filename)
for i in range(len(label)):

    img = load_image(train_addr[i])
    lab = label[i]
    # Create a feature
    feature = {'train/label': _int64_feature(lab),
               'train/image': _bytes_feature(tf.compat.as_bytes(img.tostring()))}
    
    
    # Create an example protocol buffer
    example = tf.train.Example(features=tf.train.Features(feature=feature))
    
    # Serialize to string and write on the file
    writer.write(example.SerializeToString())
    
writer.close()
sys.stdout.flush()

C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.1.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.2.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.3.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.4.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.1.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.2.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.3.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.4.jpg
C:\Users\aim\Downloads\cat-and-dog\training_set\dogs\dog.5.jpg


In [20]:
print(train_addr[0])
img = cv2.imread(train_addr[0])

C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.1.jpg


In [21]:
import matplotlib.pyplot as plt
plt.imshow(img)
plt.show()

<Figure size 640x480 with 1 Axes>

In [22]:
img = load_image(train_addr[0])

C:\Users\aim\Downloads\cat-and-dog\training_set\cats\cat.1.jpg


In [23]:
type(img)

numpy.ndarray

In [24]:
img

array([[[ 40.,  44.,  39.],
        [ 42.,  44.,  40.],
        [ 44.,  45.,  41.],
        ...,
        [181., 207., 211.],
        [169., 201., 204.],
        [163., 198., 201.]],

       [[ 41.,  45.,  40.],
        [ 42.,  44.,  40.],
        [ 43.,  45.,  41.],
        ...,
        [174., 200., 204.],
        [166., 197., 200.],
        [161., 194., 198.]],

       [[ 40.,  44.,  39.],
        [ 41.,  43.,  39.],
        [ 41.,  42.,  38.],
        ...,
        [169., 193., 197.],
        [165., 194., 199.],
        [166., 197., 202.]],

       ...,

       [[ 29.,  28.,  30.],
        [ 26.,  24.,  26.],
        [ 22.,  21.,  23.],
        ...,
        [ 25.,  31.,  44.],
        [ 21.,  27.,  39.],
        [ 33.,  39.,  50.]],

       [[ 30.,  30.,  32.],
        [ 27.,  26.,  28.],
        [ 22.,  21.,  23.],
        ...,
        [ 21.,  28.,  41.],
        [ 22.,  29.,  41.],
        [ 35.,  43.,  53.]],

       [[ 30.,  29.,  31.],
        [ 26.,  25.,  27.],
        [ 21.,  

In [25]:
img.tostring()

b'\x00\x00 B\x00\x000B\x00\x00\x1cB\x00\x00(B\x00\x000B\x00\x00 B\x00\x000B\x00\x004B\x00\x00$B\x00\x00@B\x00\x004B\x00\x00$B\x00\x00DB\x00\x000B\x00\x00 B\x00\x00HB\x00\x00,B\x00\x00 B\x00\x00\x94B\x00\x00\x88B\x00\x00\x82B\x00\x00XB\x00\x00DB\x00\x008B\x00\x00\x10B\x00\x00\x0cB\x00\x00\xf8A\x00\x00@B\x00\x00@B\x00\x000B\x00\x00\\B\x00\x00dB\x00\x00TB\x00\x00\x1cB\x00\x00,B\x00\x00\x14B\x00\x00<B\x00\x00<B\x00\x00$B\x00\x008B\x00\x00<B\x00\x00\x18B\x00\x00DB\x00\x00DB\x00\x00$B\x00\x00\x18B\x00\x00\x1cB\x00\x00\xf0A\x00\x004B\x00\x008B\x00\x00\x14B\x00\x00 B\x00\x00$B\x00\x00\x00B\x00\x000B\x00\x004B\x00\x00\x10B\x00\x000B\x00\x004B\x00\x00\x10B\x00\x00\x0cB\x00\x00\x0cB\x00\x00\xd8A\x00\x00pB\x00\x00tB\x00\x00PB\x00\x00(B\x00\x00,B\x00\x00\x08B\x00\x008B\x00\x00<B\x00\x00\x18B\x00\x00\x10B\x00\x00\x0cB\x00\x00\xf8A\x00\x00\x18B\x00\x00\x14B\x00\x00\x04B\x00\x00\x14B\x00\x00\x10B\x00\x00\x00B\x00\x00 B\x00\x00\x18B\x00\x00\x08B\x00\x004B\x00\x00,B\x00\x00\x1cB\x00\x008B\x00\x00,B\x00\

In [26]:
tf.compat.as_bytes(img.tostring())

b'\x00\x00 B\x00\x000B\x00\x00\x1cB\x00\x00(B\x00\x000B\x00\x00 B\x00\x000B\x00\x004B\x00\x00$B\x00\x00@B\x00\x004B\x00\x00$B\x00\x00DB\x00\x000B\x00\x00 B\x00\x00HB\x00\x00,B\x00\x00 B\x00\x00\x94B\x00\x00\x88B\x00\x00\x82B\x00\x00XB\x00\x00DB\x00\x008B\x00\x00\x10B\x00\x00\x0cB\x00\x00\xf8A\x00\x00@B\x00\x00@B\x00\x000B\x00\x00\\B\x00\x00dB\x00\x00TB\x00\x00\x1cB\x00\x00,B\x00\x00\x14B\x00\x00<B\x00\x00<B\x00\x00$B\x00\x008B\x00\x00<B\x00\x00\x18B\x00\x00DB\x00\x00DB\x00\x00$B\x00\x00\x18B\x00\x00\x1cB\x00\x00\xf0A\x00\x004B\x00\x008B\x00\x00\x14B\x00\x00 B\x00\x00$B\x00\x00\x00B\x00\x000B\x00\x004B\x00\x00\x10B\x00\x000B\x00\x004B\x00\x00\x10B\x00\x00\x0cB\x00\x00\x0cB\x00\x00\xd8A\x00\x00pB\x00\x00tB\x00\x00PB\x00\x00(B\x00\x00,B\x00\x00\x08B\x00\x008B\x00\x00<B\x00\x00\x18B\x00\x00\x10B\x00\x00\x0cB\x00\x00\xf8A\x00\x00\x18B\x00\x00\x14B\x00\x00\x04B\x00\x00\x14B\x00\x00\x10B\x00\x00\x00B\x00\x00 B\x00\x00\x18B\x00\x00\x08B\x00\x004B\x00\x00,B\x00\x00\x1cB\x00\x008B\x00\x00,B\x00\

In [27]:
print(type(img.tostring()))
print(type(tf.compat.as_bytes(img.tostring())))

<class 'bytes'>
<class 'bytes'>


`Basically, it comes from the fact that in Python 2, strings were dealt with primarily as bytes, not unicode.
In Python 3, all strings are natively unicode.
The purpose of the function is to ensure that whichever Python version you're using, you won't be bothered, hence the compat module name standing for compatibility.`

> ref <https://stackoverflow.com/questions/37689802/what-is-tensorflow-compat-as-str#42379195>

In [28]:
len(tf.compat.as_bytes(img.tostring()))

602112

In [29]:
len(img.tostring())

602112

In [30]:
feature = {'label_1': _int64_feature(0),
           'value_1': _float_feature(67.8),
           'label_2': _int64_feature(1),
           'value_2': _bytes_feature('today')}

TypeError: 'today' has type <class 'str'>, but expected one of: (<class 'bytes'>,)

In [31]:
feature = {'label_1': _int64_feature(0),
           'value_1': _float_feature(67.8),
           'label_2': _int64_feature(1),
           'value_2': _bytes_feature(tf.compat.as_bytes('today'))}

In [32]:
print(feature)

{'label_1': int64_list {
  value: 0
}
, 'value_1': float_list {
  value: 67.8
}
, 'label_2': int64_list {
  value: 1
}
, 'value_2': bytes_list {
  value: "today"
}
}


In [33]:
print(_float_feature(34))
print(_int64_feature(9))
print(_bytes_feature(tf.compat.as_bytes('common')))

float_list {
  value: 34.0
}

int64_list {
  value: 9
}

bytes_list {
  value: "common"
}



In [34]:
tf.train.Example(features = tf.train.Features(feature = feature))

features {
  feature {
    key: "label_1"
    value {
      int64_list {
        value: 0
      }
    }
  }
  feature {
    key: "label_2"
    value {
      int64_list {
        value: 1
      }
    }
  }
  feature {
    key: "value_1"
    value {
      float_list {
        value: 67.8
      }
    }
  }
  feature {
    key: "value_2"
    value {
      bytes_list {
        value: "today"
      }
    }
  }
}

In [35]:
example_proto = tf.train.Example(features = tf.train.Features(feature = feature))
example_proto.SerializeToString()

b'\nO\n\x10\n\x07label_1\x12\x05\x1a\x03\n\x01\x00\n\x13\n\x07value_1\x12\x08\x12\x06\n\x04\x9a\x99\x87B\n\x10\n\x07label_2\x12\x05\x1a\x03\n\x01\x01\n\x14\n\x07value_2\x12\t\n\x07\n\x05today'